### Instruction:
This script is to conduct Entity Alignment between DrugMechDB and RTX-KG2 (version 2.8.4c and 2.9.0c). 
The script is generalizable but recommend to update the Node ID's to latest Biolink standards before running the code.

DrugMechDB mechanism of action (pathway) file is located [here](https://github.com/SuLab/DrugMechDB/blob/main/indication_paths.yaml).

To obtain access to KG2 graph data, contact [RTX-KG2 team](https://github.com/RTXteam/RTX-KG2).

In [1]:
import os
import json
import pandas as pd
import yaml
import sys  # Import sys to change the field size limit
import csv


#Set working directory
os.chdir('/your/working/directory/path')

### Node ID conversion/update

In [2]:
# Open DrugMechDB YAML file
def load_yaml_file(file_path):
    try:
        with open(file_path, 'r') as file:
            return yaml.safe_load(file)
    except Exception as e:
        print(f"An error occurred: {e}")

drug_db = load_yaml_file('indication_paths.yaml') # Change the pathway where your yaml file is located

# Displays the yaml file
#drug_db 

In [3]:
### Parse YAML file extracting Node ID and their associated Names for each graph

def extract_graph_node_data(drug_db):
    # Initialize a list to store the extracted data
    node_data = []
    
    for graph in drug_db:
        graph_id = graph['graph']['_id']  # Accessing the graph ID
        nodes = graph['nodes']
        node_list = []

        for node in nodes:
            node_id = node['id']
            node_name = node['name']
            node_list.append({'id': node_id, 'name': node_name})

        node_data.append({
            'graph': {
                '_id': graph_id,
                'nodes': node_list
            }
        })

    return node_data  # list of dictionaries with nested 'nodes' under 'graph'

graphs = extract_graph_node_data(drug_db)
#graphs


In [4]:
# Screen for outdated node id's

def extract_unique_prefixes(graphs):
    unique_prefixes = set()  # Using a set to automatically handle uniqueness

    for graph in graphs:
        for node in graph['graph']['nodes']:
            prefix = node['id'].split(':', 1)[0]  # Extract prefix before the colon
            unique_prefixes.add(prefix)  # Add to the set, duplicates will not be added

    return unique_prefixes

unique_prefixes = extract_unique_prefixes(graphs)

# Print the set of unique prefixes; shows all the prefixes that are in DrugMechDB
print("DrugMechDB Node ID prefixes:",unique_prefixes)


DrugMechDB Node ID prefixes: {'taxonomy', 'TIGR', 'MESH', 'PR', 'Pfam', 'UniProt', 'CL', 'GO', 'reactome', 'HP', 'CHEBI', 'DB', 'UBERON', 'InterPro'}


In [5]:
# Update DrugMechDB Node ID prefixes
curie_prefixes = {
    "ATC": "ATC",
    "BIOLINK": "biolink",
    "BIOLINK_SOURCE": "biolink_download_source",
    "CHEBI": "CHEBI",
    "CHEMBL_COMPOUND": "CHEMBL.COMPOUND",
    "CHEMBL_MECHANISM": "CHEMBL.MECHANISM",
    "CHEMBL_TARGET": "CHEMBL.TARGET",
    "CHV": "CHV",
    "CLINICALTRIALS": "clinicaltrials",
    "DCTERMS": "dcterms",
    "DGIDB": "DGIdb",
    "DOID": "DOID",
    "DRUGBANK": "DRUGBANK",
    "DRUGCENTRAL": "DrugCentral",
    "ENSEMBL": "ENSEMBL",
    "ENSEMBL_GENOMES": "EnsemblGenomes",
    "FMA": "FMA",
    "GO": "GO",
    "GTPI": "GTPI",
    "GTPI_SOURCE": "GTPI_source",
    "HCPCS": "HCPCS",
    "HGNC": "HGNC",
    "HMDB": "HMDB",
    "HP": "HP",
    "IAO": "IAO",
    "ICD10PCS": "ICD10PCS",
    "ICD9": "ICD9",
    "IDENTIFIERS_ORG_REGISTRY": "identifiers_org_registry",
    "ISBN": "ISBN",
    "KEGG": "KEGG",
    "KEGG_COMPOUND": "KEGG.COMPOUND",
    "KEGG_DRUG": "KEGG.DRUG",
    "KEGG_ENZYME": "KEGG.ENZYME",
    "KEGG_GLYCAN": "KEGG.GLYCAN",
    "KEGG_REACTION": "KEGG.REACTION",
    "KEGG_SOURCE": "KEGG_source",
    "MEDDRA": "MEDDRA",
    "MESH": "MESH",
    "MIRBASE": "miRBase",
    "MONDO": "MONDO",
    "NCBI_GENE": "NCBIGene",
    "NCBI_TAXON": "NCBITaxon",
    "NCIT": "NCIT",
    "NDDF": "NDDF",
    "OBO": "OBO",
    "OBO_FORMAT": "oboFormat",
    "OIO": "OIO",
    "OMIM": "OMIM",
    "OWL": "owl",
    "PATHWHIZ": "PathWhiz",
    "PATHWHIZ_COMPOUND": "PathWhiz.Compound",
    "PATHWHIZ_NUCLEIC_ACID": "PathWhiz.NucleicAcid",
    "PATHWHIZ_ELEMENT_COLLECTION": "PathWhiz.ElementCollection",
    "PATHWHIZ_REACTION": "PathWhiz.Reaction",
    "PATHWHIZ_BOUND": "PathWhiz.Bound",
    "PATHWHIZ_PROTEIN_COMPLEX": "PathWhiz.ProteinComplex",
    "PDQ": "PDQ",
    "PMID": "PMID",
    "PSY": "PSY",
    "RDF": "rdf",
    "RDFS": "rdfs",
    "REACTOME": "REACT",
    "REPODB": "REPODB",
    "RHEA": "RHEA",
    "RHEA_COMP": "RHEA.COMP",
    "RO": "RO",
    "RTX": "RTX",
    "RXNORM": "RXNORM",
    "SEMMEDDB": "SEMMEDDB",
    "SKOS": "skos",
    "SMPDB": "SMPDB",
    "SNOMED": "SNOMED",
    "TTD_DRUG": "ttd.drug",
    "TTD_TARGET": "ttd.target",
    "UMLS": "UMLS",
    "UMLS_STY": "STY",
    "UMLS_SOURCE": "umls_source",
    "UNICHEM_SOURCE": "UNICHEM_source",
    "UNIPROT": "UniProtKB",
    "VANDF": "VANDF"
} #curies_prefix is prefiexes from RTX-KG2 
    
def update_node_ids(graphs, curie_prefixes):
    # Convert all dictionary keys to uppercase for case-insensitive matching
    curie_prefixes = {k.upper(): v for k, v in curie_prefixes.items()}
    unmatched_prefixes = set()
    
    for graph in graphs:
        for node in graph['graph']['nodes']:
            original_id = node['id']
            prefix, id_suffix = original_id.split(':', 1)
            upper_prefix = prefix.upper()  # Convert prefix to uppercase
            
            if upper_prefix in curie_prefixes:
                # Use the uppercased prefix to fetch the correct replacement
                node['id'] = f"{curie_prefixes[upper_prefix]}:{id_suffix}"
            else:
                unmatched_prefixes.add(prefix)  # Collect unmatched prefixes
    if unmatched_prefixes:
        print("Unmatched prefixes:", unmatched_prefixes)
        print()
    return graphs

graphs_converted = update_node_ids(graphs, curie_prefixes) 

Unmatched prefixes: {'taxonomy', 'TIGR', 'PR', 'Pfam', 'CL', 'DB', 'UBERON', 'InterPro'}



In [6]:
# Displays updated node IDs for each graph and unmatched node id prefixes
# The unmatched node ID's will be processed in the later script using name query match

#graphs_converted

In [7]:
## Save updated graph (node ID updated)

#def save_graphs_to_yaml(graphs, filename):
    #with open(filename, 'w') as file:
        #yaml.dump(graphs, file)

# Save the data to a YAML file
#save_graphs_to_yaml(graphs_converted, 'NodeID_updated_graphs.yaml')


## Entity Normalization 

In [8]:
# Open the updated node id prefix graph
def load_yaml_file(file_path):
    try:
        with open(file_path, 'r') as file:
            return yaml.safe_load(file)
    except Exception as e:
        print(f"An error occurred: {e}")

df_graph = load_yaml_file('NodeID_updated_graphs.yaml')

# Display updated node id's of DrugMechDB

In [9]:
# Open KG2 TSV/CSV file
def load_tsv_file(file_path, separator='\t', encoding='utf-8', low_memory=False):
    try:
        dtype_spec = {8: str}
        df = pd.read_csv(file_path, sep=separator, encoding=encoding, low_memory=low_memory,dtype=dtype_spec)
        return df
    except Exception as e:
        print(f"An error occurred while loading the file: {e}")

# Load KG2 Node TSV file
df_kg = load_tsv_file('KG2.9.0c/combined_nodes.tsv') # use appropriate file pathway for KG2
df_kg = df_kg[['id:ID','all_names:string[]','equivalent_curies:string[]']]

## Entity Alignment

DrugMechDB Node ID match to KG2 equivalent queries. If there is a match, it will query the canonical ID of KG2.

In [10]:
## KG2 is a large file which takes long time to process
## for the sake of efficiency we will use subset of KG2 node features/columns that are relevant for this analysis: 'id:ID','all_names:string[]','equivalent_curies:string[]'

curie_dict = {}

# Preprocess the KG2
for idx, row in df_kg.iterrows():
    if pd.notna(row['equivalent_curies:string[]']):
        curies = row['equivalent_curies:string[]'].split('ǂ')
        for curie in curies:
            clean_curie = curie.strip()
            if clean_curie:  # Make sure it's not empty
                curie_dict.update({clean_curie:row['id:ID']})


In [11]:
## Save Result & Statistics
results = []
no_matches = set()

# Process each graph
for graph in df_graph:
    graph_id = graph['graph']['_id']
    total_nodes = len(graph['graph']['nodes'])
    match_count = 0
    nodes_list = []

    print(f"Processing graph ID {graph_id}:")
    for node in graph['graph']['nodes']:
        node_id = node['id']#.lower()

        if node_id in curie_dict:
            matched_id = curie_dict[node_id]
            nodes_list.append({'id': node['id'], 'c_id': matched_id})
            print(f"Matched KG2 canonical node ID for {node['id']}: {matched_id}")
            match_count += 1
        else:
            nodes_list.append({'id': node['id'], 'c_id': '0'})  # "No matching ID found"
            no_matches.add(node['name'].lower())
            print(f"No matching KG2 canonical ID found for {node['id']}")

    # Calculate percentage matched
    pct_matched = (match_count / float(total_nodes)) * 100 if total_nodes > 0 else 0
    
    # Displays the result
    print(f"Total matches in graph {graph_id}: {match_count} out of {total_nodes} ({pct_matched} %)")
    print()
    
    # Store the result and statistics in YAML format
    results.append({
        'graph': {
            '_id': graph_id,
            'nodes': nodes_list,
            'match_count': match_count,
            'pct_matched': pct_matched,
            'total_nodes': total_nodes
        }
    })

# Save the result & statistics 
with open('DrugDB_nodeID_match.yaml', 'w') as file:
    yaml.dump(results, file, default_flow_style=False)


Processing graph ID DB00619_MESH_D015464_1:
Matched KG2 canonical node ID for MESH:D000068877: PUBCHEM.COMPOUND:123596
Matched KG2 canonical node ID for UniProtKB:P00519: NCBIGene:25
Matched KG2 canonical node ID for MESH:D015464: MONDO:0011996
Total matches in graph DB00619_MESH_D015464_1: 3 out of 3 (100.0 %)

Processing graph ID DB00619_MESH_D034721_1:
Matched KG2 canonical node ID for MESH:D000068877: PUBCHEM.COMPOUND:123596
Matched KG2 canonical node ID for UniProtKB:P10721: NCBIGene:3815
Matched KG2 canonical node ID for UniProtKB:P16234: NCBIGene:5156
Matched KG2 canonical node ID for GO:0008283: GO:0008283
Matched KG2 canonical node ID for MESH:D034721: MONDO:0016586
Total matches in graph DB00619_MESH_D034721_1: 5 out of 5 (100.0 %)

Processing graph ID DB00316_MESH_D010146_1:
Matched KG2 canonical node ID for MESH:D000082: PUBCHEM.COMPOUND:1983
Matched KG2 canonical node ID for UniProtKB:P23219: NCBIGene:5742
Matched KG2 canonical node ID for UniProtKB:P35354: NCBIGene:5743
M

### Match with name

DrugMechDB nodes that are not matched via node ID will be screened for match using node 'name' and display the associated canonical ID. 

In [12]:
# Nodes that are not matched via node id will be processed using node NAME

names_dict = {}

# Preprocess the KG2
for idx, row in df_kg.iterrows():
    if pd.notna(row['all_names:string[]']):
        names = row['all_names:string[]'].lower().split('ǂ')
        for name in names:
            clean_name = name.strip()
            if clean_name:  # Make sure it's not empty
                #names_dict.setdefault(clean_name,[]).append(row['id:ID'])
                if clean_name not in names_dict:
                    names_dict[clean_name] = set()  # Initialize a new set for this name
                names_dict[clean_name].add(row['id:ID'])  # Use set's add method to avoid duplicates

# Convert sets to lists if necessary (optional, if you need to serialize or work with JSON later)
for key in names_dict:
    names_dict[key] = list(names_dict[key])


In [13]:
results_2 = []

for graph in df_graph:
    graph_id = graph['graph']['_id']
    total_nodes = len(graph['graph']['nodes'])
    match_count = 0
    nodes_list = []

    print(f"Processing graph ID {graph_id}:")
    for node in graph['graph']['nodes']:
        node_id = node['id']#.lower()

        if node_id in curie_dict:
            matched_id = curie_dict[node_id]
            nodes_list.append({'id': node['id'], 'c_id': matched_id})
            print(f"Matched node ID for {node['id']}: {matched_id}")
            match_count += 1
            
        else:
            node_name = node['name'].lower()
            if node_name in names_dict:
                matched_ids = names_dict[node_name]
                nodes_list.append({'id': node['id'], 'c_id': matched_ids})
                print(f"Matched node name for {node['id']}: {matched_ids}")
                match_count += 1
            else:
                nodes_list.append({'id': node['id'], 'c_id': '0'})  # "No matching ID found"
                print(f"No match found for {node['id']}")

    # Calculate percentage matched
    pct_matched = (match_count / float(total_nodes)) * 100 if total_nodes > 0 else 0
    
    # Displays the result
    print(f"Total matches in graph {graph_id}: {match_count} out of {total_nodes} ({pct_matched} %)")
    print()
    
    # Store the result and statistics in YAML format
    results_2.append({
        'graph': {
            '_id': graph_id,
            'nodes': nodes_list,
            'match_count': match_count,
            'pct_matched': pct_matched,
            'total_nodes': total_nodes
        }
    })

# Save the result & statistics 
with open('DrugDB_nodeName_match.yaml', 'w') as file:
    yaml.dump(results_2, file, default_flow_style=False)

Processing graph ID DB00619_MESH_D015464_1:
Matched node ID for MESH:D000068877: PUBCHEM.COMPOUND:123596
Matched node ID for UniProtKB:P00519: NCBIGene:25
Matched node ID for MESH:D015464: MONDO:0011996
Total matches in graph DB00619_MESH_D015464_1: 3 out of 3 (100.0 %)

Processing graph ID DB00619_MESH_D034721_1:
Matched node ID for MESH:D000068877: PUBCHEM.COMPOUND:123596
Matched node ID for UniProtKB:P10721: NCBIGene:3815
Matched node ID for UniProtKB:P16234: NCBIGene:5156
Matched node ID for GO:0008283: GO:0008283
Matched node ID for MESH:D034721: MONDO:0016586
Total matches in graph DB00619_MESH_D034721_1: 5 out of 5 (100.0 %)

Processing graph ID DB00316_MESH_D010146_1:
Matched node ID for MESH:D000082: PUBCHEM.COMPOUND:1983
Matched node ID for UniProtKB:P23219: NCBIGene:5742
Matched node ID for UniProtKB:P35354: NCBIGene:5743
Matched node ID for UniProtKB:Q15185: NCBIGene:10728
Matched node ID for GO:0001516: GO:0001516
Matched node ID for MESH:D011453: PUBCHEM.COMPOUND:6145931


##### Note:
The `DrugDB_nodeID_match` or `DrugDB_nodeName_match` YAML files contain the node id of DrugMechDB and the associated canonical ID or IDs from KG2 (denoted as `c_id`). The file contains nodes percent matched (`pct_matched`), number of nodes matched (`match_count`) and total nodes (`total_nodes`) for each graph id of DrugMechDB.

`DrugDB_nodeID_match.yaml` entity alignment result using DrugMechDB node id only.
`DrugDB_nodeName_match.yaml` entity alignment result using node name if node id match is not found in KG2 `equivalent_curies:string[]`.